In [4]:
import os,sys
import tensorflow as tf
# import importlib
sys.path.append('/home/tanmay/JHU/project/deep-mediation/manuscript/code/deep-mediation/src')
import auxiliaryfunctions
# importlib.reload(auxiliaryfunctions)
import statsmodels.api as sm
import statsmodels.formula.api as smf
import seaborn as sns
import numpy as np
from scipy.stats import zscore,norm
from keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import os
import pandas as pd
import random as python_random

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error,make_scorer,mean_absolute_error,r2_score

# from datagenerator import dataGenerator
from keras import backend as K

from tensorflow.keras.callbacks import LearningRateScheduler, ModelCheckpoint, EarlyStopping
from keras.optimizers import Adam, SGD

In [5]:
np.random.seed(123)
python_random.seed(123)
tf.random.set_seed(1234)

early_stopping = True
epochs = 1000
batch_size = 32
use_dynamic_LR=False
# optimizer='Adam'
algo = 'shallow' #['shallow','deep','svr'] 
patience = 20
result_path = '/home/tanmay/JHU/project/deep-mediation/manuscript/code/deep-mediation/results/simulation-3'
num_subs = [100,500,1000]
num_iters = 20
num_runs = 100
new_shape = [28,28]

In [6]:


def create_empty_df(num_runs,num_iters):
    # Creates an empty dataFrame
    a = np.empty((num_runs,num_iters))
    a[:] = np.nan
    dataFrame = None
    parameters = ['alpha0', 'beta0','alpha','beta','gamma']
    for params in parameters:
        iter = ['iter_'+str(i) for i in range(num_iters)]
        pdindex = pd.MultiIndex.from_product([[params], iter],
                                             names=['parameters', 'runs']) 
        frame = pd.DataFrame(a, columns = pdindex,index = range(0,num_runs))
        dataFrame = pd.concat([dataFrame,frame],axis=1)
    return dataFrame

def simulate_mediation(df,M,params_df,model,algo,num_subs,batch_size,epochs,n,n_runs,iterations):
    """
    """
    early_stopping=True
    # Initialize z with some phi
    print("Using intial random model parameters")

    z = model.predict(M) 
    try:
        z = np.concatenate(z)
    except:
        pass
    
    for i in range(0,iterations):
        print('Starting iteration... %s'%(i+1))
        #Check for sign change
        if np.corrcoef(z,df.Y)[0,1] < 0 :
            z = z*(-1)
        # Check for scaling
        z= zscore(z)
        lm = smf.ols(formula='z ~ X', data=df).fit()
        alpha0 = lm.params.loc['Intercept']
        alph = lm.params.loc['X'] 

        lm = smf.ols(formula='Y ~ z + X', data=df).fit()
        beta0 = lm.params.Intercept 
        bet = lm.params.z
        gam = lm.params.X 
        resid_std = np.std(lm.resid)
        e = df.Y - beta0 - (df.X*gam)
        h = alpha0 + df.X*alph
        d = (((bet*e)+h)/((bet**2)+1))

        if algo== 'svr':
            model = auxiliaryfunctions.create_svr_model(M,d)
            z = model.predict(M)
        else:
            adam = Adam()
            model.compile(loss='mean_absolute_error',optimizer=adam)
            if early_stopping:
                es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=20)
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,callbacks=[es],
                                  shuffle=True,validation_split = 0.3)
            else:
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,
                              shuffle=True,validation_split = 0.3)
            z = model.predict(M)
       
        params_df.loc[n_runs]['alpha0','iter_'+str(i)]=alpha0
        params_df.loc[n_runs]['beta0','iter_'+str(i)]=beta0
        params_df.loc[n_runs]['beta','iter_'+str(i)]=bet
        params_df.loc[n_runs]['gamma','iter_'+str(i)]=gam
        params_df.loc[n_runs]['alpha','iter_'+str(i)]=alph

        try:
            z = np.concatenate(z)
        except:
            pass
       
    return params_df,z,model


In [7]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"

for n in num_subs:
    start = 0
    output_df = create_empty_df(num_runs,num_iters)
    for runs in range(start,num_runs):
        K.clear_session()
        print("Running simulation for image shape %s starting with %s runs"%(n,runs+1))
    # simulate the dataset
        df,mediator,z = auxiliaryfunctions.simulate_dataset(n,resize= True,
                                          new_shape=new_shape,algo=algo,visualize=False,alpha=0)
        # create a model 
        if algo == 'svr':
            model = auxiliaryfunctions.create_svr_model(mediator,df.m)
        elif algo== 'shallow':
            input_shape = (new_shape[0],new_shape[1]*4,1)
            model = auxiliaryfunctions.create_shallow_model2D(input_shape=input_shape)
        else:
            input_shape = (new_shape[0],new_shape[1]*4,1)
            model = auxiliaryfunctions.create_deep_model2D(input_shape=input_shape)

        params_df,z_final,model_ = simulate_mediation(df,mediator,output_df,
                                      model,algo,n,batch_size,epochs,
                                      n,runs,num_iters)
        params_df.to_excel(os.path.join(result_path,'simulation-3-num-subs-'+str(n)+'-'+algo+'.xlsx'))

Running simulation for image shape 500 starting with 1 runs
Using intial random model parameters
Starting iteration... 1
Epoch 1/1000
88/88 [==============================] - 0s 5ms/step - loss: 18.0900 - val_loss: 0.2909
Epoch 2/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.3361 - val_loss: 0.1624
Epoch 3/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2186 - val_loss: 0.1384
Epoch 4/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1960 - val_loss: 0.1303
Epoch 5/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1848 - val_loss: 0.1197
Epoch 6/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1618 - val_loss: 0.1088
Epoch 7/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1683 - val_loss: 0.1066
Epoch 8/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1489 - val_loss: 0.1060
Epoch 9/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.13

Epoch 81/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1050 - val_loss: 0.0834
Epoch 82/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1020 - val_loss: 0.0840
Epoch 83/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.0953 - val_loss: 0.0843
Epoch 84/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.0977 - val_loss: 0.0841
Epoch 85/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1001 - val_loss: 0.0850
Epoch 86/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1015 - val_loss: 0.0833
Epoch 87/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.0940 - val_loss: 0.0824
Epoch 88/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1026 - val_loss: 0.0831
Epoch 89/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.0939 - val_loss: 0.0832
Epoch 90/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1059 - val_los

88/88 [==============================] - 0s 3ms/step - loss: 0.2072 - val_loss: 0.2261
Epoch 4/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2154 - val_loss: 0.2256
Epoch 5/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2214 - val_loss: 0.2362
Epoch 6/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2062 - val_loss: 0.2275
Epoch 7/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2176 - val_loss: 0.2203
Epoch 8/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2029 - val_loss: 0.2247
Epoch 9/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2164 - val_loss: 0.2252
Epoch 10/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2319 - val_loss: 0.2220
Epoch 11/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2086 - val_loss: 0.2154
Epoch 12/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2268 - val_loss: 0.2193
Epoch 13/1

88/88 [==============================] - 0s 3ms/step - loss: 0.1803 - val_loss: 0.2211
Epoch 12/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1849 - val_loss: 0.2211
Epoch 13/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1969 - val_loss: 0.2298
Epoch 14/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1796 - val_loss: 0.2263
Epoch 15/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1925 - val_loss: 0.2263
Epoch 16/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1757 - val_loss: 0.2250
Epoch 17/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1973 - val_loss: 0.2315
Epoch 18/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1884 - val_loss: 0.2251
Epoch 19/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1982 - val_loss: 0.2268
Epoch 20/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1879 - val_loss: 0.2296
Epoc

88/88 [==============================] - 0s 3ms/step - loss: 0.1590 - val_loss: 0.2228
Epoch 12/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1701 - val_loss: 0.2258
Epoch 13/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1775 - val_loss: 0.2302
Epoch 14/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1683 - val_loss: 0.2280
Epoch 15/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1756 - val_loss: 0.2282
Epoch 16/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1650 - val_loss: 0.2266
Epoch 17/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1742 - val_loss: 0.2274
Epoch 18/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1758 - val_loss: 0.2266
Epoch 19/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1820 - val_loss: 0.2307
Epoch 20/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1749 - val_loss: 0.2335
Epoc

...

Epoch 24/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2199 - val_loss: 0.2677
Epoch 25/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2254 - val_loss: 0.2709
Epoch 26/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2486 - val_loss: 0.2714
Epoch 27/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2300 - val_loss: 0.2717
Epoch 28/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2314 - val_loss: 0.2736
Epoch 29/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2291 - val_loss: 0.2765
Epoch 30/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2344 - val_loss: 0.2711
Epoch 00030: early stopping
Starting iteration... 5
Epoch 1/1000
88/88 [==============================] - 0s 5ms/step - loss: 0.2559 - val_loss: 0.3168
Epoch 2/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2111 - val_loss: 0.2795
Epoch 3/1000
88/88 [=====================

Epoch 18/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1847 - val_loss: 0.2729
Epoch 19/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2131 - val_loss: 0.2819
Epoch 20/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2054 - val_loss: 0.2671
Epoch 21/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2125 - val_loss: 0.2705
Epoch 22/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2054 - val_loss: 0.2681
Epoch 23/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.2092 - val_loss: 0.2651
Epoch 00023: early stopping
Starting iteration... 8
Epoch 1/1000
88/88 [==============================] - 0s 5ms/step - loss: 0.1920 - val_loss: 0.2462
Epoch 2/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1732 - val_loss: 0.2792
Epoch 3/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1550 - val_loss: 0.2727
Epoch 4/1000
88/88 [======================

Epoch 6/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1446 - val_loss: 0.2466
Epoch 7/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1481 - val_loss: 0.2632
Epoch 8/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1550 - val_loss: 0.2492
Epoch 9/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1585 - val_loss: 0.2614
Epoch 10/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1437 - val_loss: 0.2555
Epoch 11/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1626 - val_loss: 0.2581
Epoch 12/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1653 - val_loss: 0.2634
Epoch 13/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1662 - val_loss: 0.2614
Epoch 14/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1856 - val_loss: 0.2656
Epoch 15/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1723 - val_loss: 0

Epoch 10/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1325 - val_loss: 0.2726
Epoch 11/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1548 - val_loss: 0.2750
Epoch 12/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1498 - val_loss: 0.2727
Epoch 13/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1617 - val_loss: 0.2699
Epoch 14/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1718 - val_loss: 0.2731
Epoch 15/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1636 - val_loss: 0.2681
Epoch 16/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1770 - val_loss: 0.2674
Epoch 17/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1558 - val_loss: 0.2725
Epoch 18/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1604 - val_loss: 0.2749
Epoch 19/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1806 - val_los

Epoch 21/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1776 - val_loss: 0.2694
Epoch 22/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1623 - val_loss: 0.2677
Epoch 23/1000
88/88 [==============================] - 0s 3ms/step - loss: 0.1792 - val_loss: 0.2674
Epoch 00023: early stopping
